In [26]:
#%pip install langchain openai chromadb tiktoken pypdf panel bokeh youtube-transcript-api pytube

In [27]:
from langchain.chains import RetrievalQA
from langchain.llms import OpenAI
from langchain.document_loaders import PyPDFLoader
from langchain.document_loaders.csv_loader import CSVLoader
from langchain.document_loaders import TextLoader
from langchain.document_loaders import UnstructuredEPubLoader
from langchain.document_loaders import UnstructuredPowerPointLoader
from langchain.document_loaders import UnstructuredWordDocumentLoader
from langchain.document_loaders import UnstructuredHTMLLoader
from langchain.document_loaders import UnstructuredURLLoader
from langchain.document_loaders import YoutubeLoader
from langchain.indexes import VectorstoreIndexCreator
from langchain.text_splitter import CharacterTextSplitter
from langchain.embeddings import OpenAIEmbeddings
from langchain.vectorstores import Chroma
import panel as pn
import os
import dotenv
dotenv.load_dotenv()
api_key = os.environ.get("API_KEY")

In [28]:

pn.extension('texteditor', template="bootstrap", sizing_mode='stretch_width')
pn.state.template.param.update(
    main_max_width="690px",
    header_background="#F08080",
)

In [29]:
file_input = pn.widgets.FileInput(width=300)

openaikey = pn.widgets.PasswordInput(
    value=api_key, placeholder="Insert your Openai API key here", width=250
)
prompt = pn.widgets.TextEditor(
    value="", placeholder="How do you become a good programmer?", height=160, toolbar=False
)
search_button = pn.widgets.Button(name="Search!")

select_k = pn.widgets.IntSlider(
    name="Number of relevant chunks", start=1, end=10, step=1, value=2
)
select_chain_type = pn.widgets.RadioButtonGroup(
    name='Chain type', 
    options=['stuff', 'map_reduce', "refine", "map_rerank"]
)

legend = pn.pane.Markdown("""
**Chain types:**

- `stuff`: Parse the entire document at one go. (for smaller documents)
- `map_reduce`: Split the document into smaller chunks in parallel. (faster processing but less detailed answer)
- `refine`: Split the document into smaller chunks subsequently. (slower processing but more detailed answer)
- `map_rerank`: Split the document and into individual chunks. (for simple questions)
""")

widgets = pn.Row(
    pn.Column(prompt, search_button, margin=5),
    pn.Card(
        "Chain type:",
        pn.Column(select_chain_type, select_k),
        title="Advanced settings", margin=10
    ), 
    pn.Column(legend)
)

In [30]:
def qa(file, query, chain_type, k):
    # load document based on filetype
    if file.endswith(".txt"):
        loader = TextLoader(file)
        documents = loader.load()
    elif file.endswith(".pdf"):
        loader = PyPDFLoader(file)
        documents = loader.load()
    elif file.endswith(".epub"):
        loader = UnstructuredEPubLoader(file)
        documents = loader.load()
    elif file.endswith(".pptx"):
        loader = UnstructuredPowerPointLoader(file)
        documents = loader.load()
    elif file.endswith(".csv"):
        loader = CSVLoader(file)
        documents = loader.load()
    elif file.endswith(".docx"):
        loader = UnstructuredWordDocumentLoader(file)
        documents = loader.load()
    elif file.endswith(".html"):
        loader = UnstructuredHTMLLoader(file)
        documents = loader.load()
    else:
        pass
    # split the documents into chunks
    text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=0)
    texts = text_splitter.split_documents(documents)
    # select which embeddings we want to use
    embeddings = OpenAIEmbeddings()
    # create the vectorestore to use as the index
    db = Chroma.from_documents(texts, embeddings)
    # expose this index in a retriever interface
    retriever = db.as_retriever(search_type="similarity", search_kwargs={"k": k})
    # create a chain to answer questions 
    qa = RetrievalQA.from_chain_type(
        llm=OpenAI(), chain_type=chain_type, retriever=retriever, return_source_documents=True)
    result = qa({"query": query})
    print(result['result'])
    return result

In [31]:
convos = []  # store all panel objects in a list

def qa_result(_):
    os.environ["OPENAI_API_KEY"] = openaikey.value
    
    # save pdf file to a temp file 
    if file_input.value is not None:
        file_input.save("/.cache/temp.pdf")
    
        prompt_text = prompt.value
        if prompt_text:
            result = qa(file="/.cache/temp.pdf", query=prompt_text, chain_type=select_chain_type.value, k=select_k.value)
            convos.extend([
                pn.Row(
                    pn.panel("\U0001F60A", width=10),
                    prompt_text,
                    width=600
                ),
                pn.Row(
                    pn.panel("\U0001F916", width=10),
                    pn.Column(
                        result["result"],
                        "Relevant source text:",
                        pn.pane.Markdown('\n--------------------------------------------------------------------\n'.join(doc.page_content for doc in result["source_documents"]))
                    )
                )
            ])
            #return convos
    return pn.Column(*convos, margin=15, width=575, min_height=400)

In [32]:
qa_interactive = pn.panel(
    pn.bind(qa_result, search_button),
    loading_indicator=True,
)

In [33]:
output = pn.WidgetBox('*Output will show up here:*', qa_interactive, width=630, scroll=True)

In [34]:
# layout
pn.Column(
    pn.pane.Markdown("""
    ## Query anything in your files/youtube video \U0001F60A!
    
    1) Upload a document(pdf,csv,epub,ppt,txt,docx, html). OR youtube link \n
    2) Enter OpenAI API key(Using Aaron's by default). \n
    3) Ask any question and click "Search" or "Search URL".
    
    """),
    pn.Row(file_input,pn.pane.HTML("OpenAI API Key: ", width=110, align="end"), openaikey),
    output,
    widgets

).servable()

Column(sizing_mode='stretch_width')
    [0] Markdown(str, sizing_mode='stretch_width')
    [1] Row(sizing_mode='stretch_width')
        [0] FileInput(width=300)
        [1] HTML(str, align='end', width=110)
        [2] PasswordInput(placeholder='Insert your O..., value='sk-AxQw5rfYepVB7zo9MxMlT3..., width=250)
    [2] TextInput(name='YouTube URL', placeholder='Enter a YouTube U..., width=600)
    [3] TextInput(name='Website URL', placeholder='Enter a website U..., width=600)
    [4] WidgetBox(scroll=True, width=630)
        [0] Markdown(str, sizing_mode='stretch_width')
        [1] ParamFunction(function, _pane=Column, loading_indicator=True, sizing_mode='stretch_width')
    [5] Row(sizing_mode='stretch_width')
        [0] Column(margin=5, sizing_mode='stretch_width')
            [0] TextEditor(height=160, placeholder='How do you become a..., sizing_mode='stretch_width', toolbar=False)
            [1] Button(name='Search!', sizing_mode='stretch_width')
        [1] Card(margin=10, sizing_mode='stretch_width', title='Advanced settings')
            [0] Markdown(str, sizing_mode='stretch_width')
            [1] Column(sizing_mode='stretch_width')
                [0] RadioButtonGroup(name='Chain type', options=['stuff', 'map_reduce', ...], sizing_mode='stretch_width', value='stuff')
                [1] IntSlider(end=10, name='Number of relevant c..., sizing_mode='stretch_width', start=1, value=2)
        [2] Column(sizing_mode='stretch_width')
            [0] Markdown(str, sizing_mode='stretch_width')